# Async Exercise: News Framing Dataset

In [46]:
import os
import pandas as pd
import numpy as np
import json
import re
import gensim
import nltk
import requests
import datetime

from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from gensim import corpora, models
from nltk.stem import WordNetLemmatizer
from bs4 import BeautifulSoup
from datetime import datetime

## News Site 1 - The Guardian

In [4]:
key1 = 'e66d4bc5-56e7-4514-a3e4-9022ecf9b7ce'

url1 = 'https://content.guardianapis.com/search?from-date=2021-03-11&to-date=2021-03-12&page-size=20&page=1&order-by=newest&show-fields=body,byline&api-key='+key1
r1 = requests.get(url1)
json_news1 = r1.json()

In [5]:
#Finding how many Pages
pages = json_news1['response']['pages']
pages

24

In [6]:
#Finding size
size = len(json_news1['response']['results'])
size

20

In [7]:
# Getting the Url of the First News Article
url_1st = json_news1['response']['results'][0]
url_1st

{'id': 'sport/2021/mar/12/rory-mcilroy-chasing-bryson-dechambeaus-power-has-cost-me',
 'type': 'article',
 'sectionId': 'sport',
 'sectionName': 'Sport',
 'webPublicationDate': '2021-03-12T23:36:03Z',
 'webTitle': 'Rory McIlroy: Chasing Bryson DeChambeau’s power has cost me',
 'webUrl': 'https://www.theguardian.com/sport/2021/mar/12/rory-mcilroy-chasing-bryson-dechambeaus-power-has-cost-me',
 'apiUrl': 'https://content.guardianapis.com/sport/2021/mar/12/rory-mcilroy-chasing-bryson-dechambeaus-power-has-cost-me',
 'fields': {'byline': 'Ewan Murray',
  'body': '<p>While Rory McIlroy’s struggles go on, Lee Westwood’s outstanding form continued. Just days after taking Bryson DeChambeau to the final hole at the Arnold Palmer Invitational, the Englishman added a 66 to his first-round 69 and leads by one shot from Matthew Fitzpatrick at the Players Championship.</p> <p>McIlroy has admitted a desire to add more length to his game, fuelled in part by DeChambeau’s power play at the 2020 US Open,

In [8]:
# Getting the Title
art_title = json_news1['response']['results'][0]['webTitle']
print(f'{art_title} \n')

# Getting the Author
if (json_news1['response']['results'][0]['fields'].get('byline')):
    art_authors = json_news1['response']['results'][0]['fields']['byline']
else:
    art_authors = 'No Author'
print(f'{art_authors}')

# Getting the Date
date = json_news1['response']['results'][0]['webPublicationDate']
match = re.search('\d{4}-\d{2}-\d{2}',date)
art_date = datetime.datetime.strptime(match.group(), '%Y-%m-%d').date()
print(f'{art_date} \n')

#Getting the content
fullcontent = json_news1['response']['results'][0]['fields']['body']
art_fullcontent = re.sub('<[^<]+?>', '', fullcontent)
art_fullcontent = re.sub(r"    [^<]+?    ", ' ', art_fullcontent)
art_fullcontent = re.sub(r"Related[^<]+?    ", ' ', art_fullcontent)
print(f'{art_fullcontent}')

Rory McIlroy: Chasing Bryson DeChambeau’s power has cost me 

Ewan Murray
2021-03-12 

While Rory McIlroy’s struggles go on, Lee Westwood’s outstanding form continued. Just days after taking Bryson DeChambeau to the final hole at the Arnold Palmer Invitational, the Englishman added a 66 to his first-round 69 and leads by one shot from Matthew Fitzpatrick at the Players Championship. McIlroy has admitted a desire to add more length to his game, fuelled in part by DeChambeau’s power play at the 2020 US Open, has triggered technical problems that were visible here. A second round of 75 at Sawgrass, added to Thursday’s 79, meant McIlroy comfortably missed the cut. Afterwards, he expanded on the basis for his swing issues. “Probably, like October last year, doing a little bit of speed training, started getting sucked into that stuff, swing got flat, long and too rotational,” said McIlroy. “Obviously I added some speed and am hitting the ball longer but what that did to my swing as a whole p

## Saving to Data Frame

In [10]:
#Inserting data into Data Frame
source = []
pubdate = []
title = []
article_body = []
author = []
for i in range(size):
    # Getting the Title
    art_title = json_news1['response']['results'][i]['webTitle']
        
        
    # Getting the Author
    if (json_news1['response']['results'][i]['fields'].get('byline')):
        art_authors = json_news1['response']['results'][i]['fields']['byline']
    else:
        art_authors = 'No Author'

        
    # Getting the Date
    date = json_news1['response']['results'][i]['webPublicationDate']
    match = re.search('\d{4}-\d{2}-\d{2}',date)
    art_date = datetime.datetime.strptime(match.group(), '%Y-%m-%d').date()
    art_date = (f'{art_date}')
        
    #Getting the content
    fullcontent = json_news1['response']['results'][i]['fields']['body']
    art_fullcontent = re.sub('<[^<]+?>', '', fullcontent)
    art_fullcontent = re.sub(r"    [^<]+?    ", ' ', art_fullcontent)
    art_fullcontent = re.sub(r"Related[^<]+?    ", ' ', art_fullcontent)
    
    
    #Saving to the arrays
    source.append("The Guardian")
    pubdate.append(art_date)
    title.append(art_title)
    article_body.append(art_fullcontent)
    author.append(art_authors)

news1={'Source': source, 'Date': pubdate, 'Title': title, 'Article': article_body, 'Author': author}
news1_df = pd.DataFrame(data=news1)

In [11]:
news1_df

Source        Date  \
0   The Guardian  2021-03-12   
1   The Guardian  2021-03-12   
2   The Guardian  2021-03-12   
3   The Guardian  2021-03-12   
4   The Guardian  2021-03-12   
5   The Guardian  2021-03-12   
6   The Guardian  2021-03-12   
7   The Guardian  2021-03-12   
8   The Guardian  2021-03-12   
9   The Guardian  2021-03-12   
10  The Guardian  2021-03-12   
11  The Guardian  2021-03-12   
12  The Guardian  2021-03-12   
13  The Guardian  2021-03-12   
14  The Guardian  2021-03-12   
15  The Guardian  2021-03-12   
16  The Guardian  2021-03-12   
17  The Guardian  2021-03-12   
18  The Guardian  2021-03-12   
19  The Guardian  2021-03-12   

                                                Title  \
0   Rory McIlroy: Chasing Bryson DeChambeau’s powe...   
1   Australia commits $100m to Covid vaccine deal ...   
2   Minneapolis to pay George Floyd's family $27m ...   
3   New York senators urge Cuomo to resign after g...   
4   High school announcer caught by hot mic blames...   
5   Labour suspends East Ham and West Ham constitu...   
6   Craven Cottage pitch is as bad as the Etihad S...   
7   Relentless Harry Kane proving to be both rewar...   
8   Thomas Tuchel has no qualms over calling out C...   
9   Newcastle 1-1 Aston Villa: Premier League – as...   
10  The Little Things review – Denzel Washington k...   
11  After 75-year-old dies from attack, alarm incr...   
12  IOC under fire after ‘dismissing’ claims of ge...   
13  Jamaal Lascelles snatches point for Newcastle ...   
14  Premier League hurtling towards £2bn black hol...   
15  New York City prosecutor leading Trump inquiry...   
16  Sarah Everard: Met police officer charged with...   
17                     Corrections and clarifications   
18  Marginal gains or medical gains? Questions rem...   
19  Team Sky and British Cycling in dock after Fre...   

                                              Article  \
0   While Rory McIlroy’s struggles go on, Lee West...   
1   A historic first meeting of leaders of the Qua...   
2   The city of Minneapolis has agreed to pay $27m...   
3   New York’s two US senators, Chuck Schumer, who...   
4   An announcer for a live stream of an Oklahoma ...   
5   Two local Labour parties have been suspended a...   
6   Pep Guardiola has criticised the pitch at the ...   
7   It was broadly hushed up last Sunday but Harry...   
8   Thomas Tuchel is not worried about upsetting C...   
9     10.23pm GMT     Steve Bruce speaks: “There w...   
10  There’s a self-serious portent to the drab ser...   
11  A 75-year-old man from Hong Kong died in Oakla...   
12  The International Olympic Committee is facing ...   
13  Jamaal Lascelles is the sort of centre-half wh...   
14  Richard Masters, the chief executive of the Pr...   
15  Manhattan’s district attorney, Cyrus Vance Jr,...   
16  A serving Metropolitan police officer has been...   
17  • An article about Piers Morgan and his commen...   
18  In that golden decade when Team Sky and Britis...   
19  Team Sky and British Cycling’s successes over ...   

                                          Author  
0                                    Ewan Murray  
1              Graham Readfearn and Daniel Hurst  
2     Amudalat Ajasa in Minneapolis and agencies  
3     Daniel Strauss, Oliver Milman and agencies  
4                Bryan Armen Graham and agencies  
5                              Aubrey Allegretti  
6                                  Jamie Jackson  
7                                   David Hytner  
8                                Jacob Steinberg  
9                              Barry Glendenning  
10                                  Benjamin Lee  
11                                     Vivian Ho  
12                                    Sean Ingle  
13               Louise Taylor at St James' Park  
14                                 Paul MacInnes  
15                   Guardian staff and agencies  
16    Vikram Dodd Police and crime correspondent  
17  Corrections and cla

## News Site 2 - The New York Times

In [12]:
key2 = 'L7GA5WnsgfCrQZFMMHdqM7u8r4IBTB7l'

url2 = 'https://api.nytimes.com/svc/archive/v1/2021/3.json?api-key='+key2
r2 = requests.get(url2)
json_news2 = r2.json()

In [14]:
json_news2

{'copyright': 'Copyright (c) 2021 The New York Times Company. All Rights Reserved.',
 'response': {'docs': [{'abstract': 'A quick guide to watching the ceremony.',
    'web_url': 'https://www.nytimes.com/2021/02/28/movies/how-to-watch-the-golden-globes-on-tv-and-online.html',
    'snippet': 'A quick guide to watching the ceremony.',
    'lead_paragraph': 'When the 78th annual Golden Globes are handed out on Sunday, they will be the first major awards show of the season, coming nearly two months after we would typically find out the best picture winner.',
    'source': 'The New York Times',
    'multimedia': [{'rank': 0,
      'subtype': 'xlarge',
      'caption': None,
      'credit': None,
      'type': 'image',
      'url': 'images/2021/02/26/arts/26globes-info/26globes-info-articleLarge.jpg',
      'height': 400,
      'width': 600,
      'subType': 'xlarge',
      'crop_name': 'articleLarge',
      'legacy': {'xlarge': 'images/2021/02/26/arts/26globes-info/26globes-info-articleLarg

In [13]:
# Getting info of 1st Article
first = json_news2['response']['docs'][0]
first

{'abstract': 'A quick guide to watching the ceremony.',
 'web_url': 'https://www.nytimes.com/2021/02/28/movies/how-to-watch-the-golden-globes-on-tv-and-online.html',
 'snippet': 'A quick guide to watching the ceremony.',
 'lead_paragraph': 'When the 78th annual Golden Globes are handed out on Sunday, they will be the first major awards show of the season, coming nearly two months after we would typically find out the best picture winner.',
 'source': 'The New York Times',
 'multimedia': [{'rank': 0,
   'subtype': 'xlarge',
   'caption': None,
   'credit': None,
   'type': 'image',
   'url': 'images/2021/02/26/arts/26globes-info/26globes-info-articleLarge.jpg',
   'height': 400,
   'width': 600,
   'subType': 'xlarge',
   'crop_name': 'articleLarge',
   'legacy': {'xlarge': 'images/2021/02/26/arts/26globes-info/26globes-info-articleLarge.jpg',
    'xlargewidth': 600,
    'xlargeheight': 400}},
  {'rank': 0,
   'subtype': 'jumbo',
   'caption': None,
   'credit': None,
   'type': 'image'

In [15]:
#Getting the page of the news article
URL = json_news2['response']['docs'][0]['web_url']
art_page = requests.get(URL)
print(art_page.content)

b'<!DOCTYPE html>\n<html lang="en" class="story nytapp-vi-article"  xmlns:og="http://opengraphprotocol.org/schema/">\n  <head>\n    <title data-rh="true">How to watch the Golden Globes on TV and Online. - The New York Times</title>\n    <meta data-rh="true" property="article:published_time" content="2021-03-01T00:01:56.000Z"/><meta data-rh="true" property="article:modified_time" content="2021-03-01T00:01:56.000Z"/><meta data-rh="true" http-equiv="Content-Language" content="en"/><meta data-rh="true" name="robots" content="noarchive"/><meta data-rh="true" name="articleid" content="100000007628794"/><meta data-rh="true" name="nyt_uri" content="nyt://article/f1320567-f5d3-53f1-a2ee-ab273a7cc763"/><meta data-rh="true" name="pubp_event_id" content="pubp://event/7ffd3f0315a64a14bec5c02092b1f6c3"/><meta data-rh="true" name="description" content="A quick guide to watching the ceremony."/><meta data-rh="true" name="image" content="https://static01.nyt.com/images/2021/02/26/arts/26globes-info/26g

In [16]:
#Getting the article
soup = BeautifulSoup(art_page.content, 'html.parser')
body = soup.find_all('div',{'class':'css-1fanzo5 StoryBodyCompanionColumn'})
body

[<div class="css-1fanzo5 StoryBodyCompanionColumn"><div class="css-53u6y8"><p class="css-axufdj evys1bk0">When the <a class="css-1g7m0tk" href="https://www.goldenglobes.com/" rel="noopener noreferrer" target="_blank" title="">78th annual Golden Globes</a> are handed out on Sunday, they will be the first major awards show of the season, coming nearly two months after we would typically find out the best picture winner.</p><p class="css-axufdj evys1bk0">The ceremony begins at 8 p.m. Eastern, 5 p.m. Pacific. The network broadcasting the ceremony, NBC, has a preshow; with Jane Lynch and Susan Kelechi Watson as hosts, it starts at 7 p.m. Eastern, 4 p.m. Pacific.</p><p class="css-axufdj evys1bk0">On television, NBC is the official broadcaster. Online, if you have a cable login, you can watch via <a class="css-1g7m0tk" href="https://www.nbc.com/live/e" rel="noopener noreferrer" target="_blank" title="">NBC.com/live</a>. Depending on where you live, there’s also <a class="css-1g7m0tk" href="ht

In [17]:
#Combining each section of the article
art_fullcontent = body[0].text.strip()
for i in range(1,len(body)):
    art_fullcontent = art_fullcontent + '\n\n' + body[i].text.strip()
    art_fullcontent = re.sub(r"\n\n\n", ' ', art_fullcontent)
print(f'{art_fullcontent}')

When the 78th annual Golden Globes are handed out on Sunday, they will be the first major awards show of the season, coming nearly two months after we would typically find out the best picture winner.The ceremony begins at 8 p.m. Eastern, 5 p.m. Pacific. The network broadcasting the ceremony, NBC, has a preshow; with Jane Lynch and Susan Kelechi Watson as hosts, it starts at 7 p.m. Eastern, 4 p.m. Pacific.On television, NBC is the official broadcaster. Online, if you have a cable login, you can watch via NBC.com/live. Depending on where you live, there’s also Hulu + Live TV, Sling TV, AT&T TV Now, YouTube TV or FuboTV, which all require subscriptions, though many are offering free trials.


In [18]:
#get headline, main - title
art_title = json_news2['response']['docs'][0]['headline']['main']
print(f'{art_title} \n')

#get pub_date - date
date = json_news2['response']['docs'][0]['pub_date']
match = re.search('\d{4}-\d{2}-\d{2}',date)
art_date = datetime.datetime.strptime(match.group(), '%Y-%m-%d').date()
print(f'{art_date} \n')

#get byline, original - author
if (json_news2['response']['docs'][0]['byline'].get('original')):
    art_authors = fullcontent = json_news2['response']['docs'][0]['byline']['original']
    art_authors = re.sub('By ', '', art_authors)
else:
    art_authors = 'No Author'
print(f'{art_authors}')

#get web_url -> scrape - full article
art_url = json_news2['response']['docs'][0]['web_url']
art_page = requests.get(art_url )
soup = BeautifulSoup(art_page.content, 'html.parser')
body = soup.find_all('div',{'class':'css-1fanzo5 StoryBodyCompanionColumn'})
art_fullcontent = body[0].text.strip()
for i in range(1,len(body)):
    art_fullcontent = art_fullcontent + '\n\n' + body[i].text.strip()
    art_fullcontent = re.sub(r"\n\n\n", ' ', art_fullcontent)
print(f'{art_fullcontent}')

How to watch the Golden Globes on TV and Online. 

2021-03-01 

Sarah Bahr
When the 78th annual Golden Globes are handed out on Sunday, they will be the first major awards show of the season, coming nearly two months after we would typically find out the best picture winner.The ceremony begins at 8 p.m. Eastern, 5 p.m. Pacific. The network broadcasting the ceremony, NBC, has a preshow; with Jane Lynch and Susan Kelechi Watson as hosts, it starts at 7 p.m. Eastern, 4 p.m. Pacific.On television, NBC is the official broadcaster. Online, if you have a cable login, you can watch via NBC.com/live. Depending on where you live, there’s also Hulu + Live TV, Sling TV, AT&T TV Now, YouTube TV or FuboTV, which all require subscriptions, though many are offering free trials.


## Saving to Data Frame

In [19]:
#Inserting data into Data Frame
source = []
pubdate = []
title = []
article_body = []
author = []
for i in range(20):
    # Getting the Title
    art_title = json_news2['response']['docs'][i]['headline']['main']
        
        
    # Getting the Author
    if (json_news2['response']['docs'][i]['byline'].get('original')):
        art_authors = fullcontent = json_news2['response']['docs'][i]['byline']['original']
        art_authors = re.sub('By ', '', art_authors)
    else:
        art_authors = 'No Author'

        
    # Getting the Date
    date = json_news2['response']['docs'][i]['pub_date']
    match = re.search('\d{4}-\d{2}-\d{2}',date)
    art_date = datetime.datetime.strptime(match.group(), '%Y-%m-%d').date()
    art_date = (f'{art_date}')
        
    #Getting the content
    art_url = json_news2['response']['docs'][i]['web_url']
    art_page = requests.get(art_url )
    soup = BeautifulSoup(art_page.content, 'html.parser')
    body = soup.find_all('div',{'class':'css-1fanzo5 StoryBodyCompanionColumn'})
    art_fullcontent = body[0].text.strip()
    for i in range(1,len(body)):
        art_fullcontent = art_fullcontent + '\n\n' + body[i].text.strip()
        art_fullcontent = re.sub(r"\n\n\n", ' ', art_fullcontent)
    
    
    #Saving to the arrays
    source.append("The New York Times")
    pubdate.append(art_date)
    title.append(art_title)
    article_body.append(art_fullcontent)
    author.append(art_authors)

news2={'Source': source, 'Date': pubdate, 'Title': title, 'Article': article_body, 'Author': author}
news2_df = pd.DataFrame(data=news2)

In [20]:
news2_df

Source        Date  \
0   The New York Times  2021-03-01   
1   The New York Times  2021-03-01   
2   The New York Times  2021-03-01   
3   The New York Times  2021-03-01   
4   The New York Times  2021-03-01   
5   The New York Times  2021-03-01   
6   The New York Times  2021-03-01   
7   The New York Times  2021-03-01   
8   The New York Times  2021-03-01   
9   The New York Times  2021-03-01   
10  The New York Times  2021-03-01   
11  The New York Times  2021-03-01   
12  The New York Times  2021-03-01   
13  The New York Times  2021-03-01   
14  The New York Times  2021-03-01   
15  The New York Times  2021-03-01   
16  The New York Times  2021-03-01   
17  The New York Times  2021-03-01   
18  The New York Times  2021-03-01   
19  The New York Times  2021-03-01   

                                                Title  \
0    How to watch the Golden Globes on TV and Online.   
1    What will win tonight? Here are our predictions.   
2   Daniel Kaluuya and Chadwick Boseman are both r...   
3   Full Text of Cuomo’s Statement in Response to ...   
4   Forget ‘Succession.’ You Can Watch ‘90 Day Fia...   
5                  Voter Suppression Is Grand Larceny   
6   CPAC Takeaways: Trump Dominates, and DeSantis ...   
7       Golden Globes Winners 2021: The Complete List   
8   Daniel Kaluuya overcomes the first hiccup of t...   
9   Transcript: Amy Poehler and Tina Fey skewer th...   
10                         Corrections: March 1, 2021   
11  Quotation of the Day: Salvador’s Combative Bos...   
12  Collin Morikawa Wins Workday Title on a Day of...   
13  Emma Corrin, as Princess Diana, wins her first...   
14                               Your Monday Briefing   
15  ‘Minari’ wins best foreign-language film, but ...   
16  ‘Allen v. Farrow’ Episode 2 Recap: A Family To...   
17  Chloé Zhao becomes the first Asian woman to wi...   
18  Transcript: Jane Fonda calls for diversity in ...   
19  Chadwick Boseman wins a best actor Golden Glob...   

                                              Article  \
0   When the 78th annual Golden Globes are handed ...   
1   The Hollywood Foreign Press Association, which...   
2   As soon as nominations were announced on Feb. ...   
3   STATEMENT FROM GOVERNOR ANDREW M. CUOMO“Questi...   
4   “Ninety Day Fiancé” is, on some Sunday nights,...   
5   In 1890, Mississippi became one of the first s...   
6   Any lingering belief that Donald J. Trump woul...   
7   Streaming services dominated Sunday night’s Go...   
8   Daniel Kaluuya experienced the first glitch of...   
9   What’s 2,800 miles between friends? On Sunday ...   
10  OPINIONAn Op-Ed essay on Tuesday about medical...   
11  “The president has had some outbursts, but the...   
12  BRADENTON, Fla. — Although he was atop the lea...   
13  Emma Corrin’s uncanny and sympathetic portraya...   
14  (Want to get this briefing by email? Here’s th...   
15  “Minari,” Lee Isaac Chung’s semi-autobiographi...   
16  At the end of Episode 1 of “Allen v. Farrow,” ...   
17  Chloé Zhao, whose drama “Nomadland” offered an...   
18  “We are a community of storytellers, aren’t we...   
19  Chadwick Boseman won his first Golden Globe, a...   

                               Author  
0                          Sarah Bahr  
1                           No Author  
2   Brooks Barnes and Nicole Sperling  
3                           No Author  
4                           Ben Smith  
5                     Charles M. Blow  
6   Shane Goldmacher and Elaina Plott  
7                           Gabe Cohn  
8                          Sarah Bahr  
9                          Maya Salam  
10                          No Author  
11                          No Author  
12                    Bill Pennington  
13                         Maya Salam  
14                      Natasha Frost  
15          Maya Salam and Robert Ito  
16                       Julia Jacobs  
17                       Matt Stevens  
18                         Maya Salam  
19                   

## News Site 3 - CNN

In [21]:
source = []
pubdate = []
title = []
article_body = []
author = []
k = 10
for i in range(3):
    CNN_URL="https://edition.cnn.com/world/live-news/coronavirus-pandemic-vaccine-updates-03-{}-21/index.html".format(k+i)
    page = requests.get(CNN_URL)
    cnn_contents = BeautifulSoup(page.content,'lxml')
    info_header = cnn_contents.find_all("header")
    article_cont = [a.text for a in cnn_contents.find_all("div", "sc-bdVaJa post-content-rendered render-stellar-contentstyles__Content-sc-9v7nwy-0 erzhuK")]
    for i in range(1,10):
        header_list = info_header[i+1]
        time_info = header_list.contents[0].text
        title_info = header_list.contents[1].text
        print(i)
        print("Source: CNN")
        if len(header_list.contents) > 2:
            author_info = header_list.contents[2].text
            print("Title: ",title_info,"\n")
            print("Time: ",time_info[14:len(title_info)],"\n")
            print("Author: ",author_info[11:len(author_info)],"\n")
        else:
            print("Title: ",title_info,"\n")
            print("Time: ",time_info,"\n")
            print("Author: None \n")
        print(article_cont[i])
    

1
Source: CNN
Title:  16 states no longer require face coverings 

Time:  March 10, 2021 

Author:  Will Brown 

Wyoming Gov. Mark Gordon gives the State of the State address to the 66th Wyoming Legislature Tuesday, March 2, inside the state Capitol.  Michael Cummo/Wyoming Tribune Eagle via APWith Gov. Greg Abbott lifting Texas’ statewide mask mandate on Wednesday, 16 states no longer require face coverings.Earlier this week, Wyoming Gov. Mark Gordon announced that he is removing the statewide mask requirement on March 16.Here are the states with no mask requirements:Alaska: Alaska does not require the use of masks, limit group size or business operations. All the state does is encourage Alaskans to do their part to limit the spread of Covid-19, recommending that residents practice social distancing and wear a mask, without any mandate. The mayor of Anchorage, though, has signed an order requiring people to wear face coverings in public.Arizona: Gov. Doug Ducey allows individual counti

## Saving to Data Frame


In [44]:
source = []
pubdate = []
title = []
article_body = []
author = []
k = 10
for i in range(3):
    CNN_URL="https://edition.cnn.com/world/live-news/coronavirus-pandemic-vaccine-updates-03-{}-21/index.html".format(k+i)
    page = requests.get(CNN_URL)
    cnn_contents = BeautifulSoup(page.content,'lxml')
    info_header = cnn_contents.find_all("header")
    article_cont = [a.text for a in cnn_contents.find_all("div", "sc-bdVaJa post-content-rendered render-stellar-contentstyles__Content-sc-9v7nwy-0 erzhuK")]
    for i in range(1,10):
        header_list = info_header[i+1]
        time_info = header_list.contents[0].text
        title_info = header_list.contents[1].text
        source.append("CNN")
        art_date = datetime.strptime(time_info[14:len(title_info)].strip(), '%B %d, %Y').date()
        art_date = (f'{art_date}')
        pubdate.append(art_date)
        title.append(title_info)
        if len(header_list.contents) > 2:
            author_info = header_list.contents[2].text
            author.append(author_info[11:len(author_info)])
        else:
            author.append("No Author")
        article_body.append(article_cont[i])
    
news3={'Source': source, 'Date': pubdate, 'Title': title, 'Article': article_body, 'Author': author}
news3_df = pd.DataFrame(data=news3)
news3_df

Source        Date                                              Title  \
0     CNN  2021-03-10         16 states no longer require face coverings   
1     CNN  2021-03-10       Here's the latest Covid-19 update from Texas   
2     CNN  2021-03-10  First participants have received Covid-19 vacc...   
3     CNN  2021-03-10  Houstonians who refuse to comply with private ...   
4     CNN  2021-03-10  Centers for Medicare & Medicaid Services offer...   
5     CNN  2021-03-10  Brazil sets another new record for daily coron...   
6     CNN  2021-03-10  Go There: CNN heads to the New York state neig...   
7     CNN  2021-03-10  Biden says US is on track to have enough Covid...   
8     CNN  2021-03-10  Biden thanks Johnson & Johnson and Merck for "...   
9     CNN  2021-03-11  6 key lines from Biden's national address on t...   
10    CNN  2021-03-11  Key model projects more than 598,000 Americans...   
11    CNN  2021-03-11  Van Jones: Biden didn't say you need me. He sa...   
12    CNN  2021-03-11  Biden: "Things may get worse again as new vari...   
13    CNN  2021-03-11  Biden says Americans "lost faith" in democracy...   
14    CNN  2021-03-11  Federal government to launch new tools to find...   
15    CNN  2021-03-11  Biden: My "fervent prayer" is to bring a divid...   
16    CNN  2021-03-11   Biden to Americans: I need you to get vaccinated   
17    CNN  2021-03-11  Biden tackles death, loss, and the toll the pa...   
18    CNN  2021-03-12  US education secretary on reopening schools: "...   
19    CNN  2021-03-12  Head of largest teachers' union says educators...   
20    CNN  2021-03-12  US students share the struggles they've faced ...   
21    CNN  2021-03-12  Education Secretary Miguel Cardona says his to...   
22    CNN  2021-03-12  Los Angeles County to reopen indoor dining, mo...   
23    CNN  2021-03-12  Given what we know now about the pandemic, the...   
24    CNN  2021-03-12  CDC removes three-month cap on fully vaccinate...   
25    CNN  2021-03-12  Treasury Department confirms first batch of Co...   
26    CNN  2021-03-12  Report: AstraZeneca will seek US authorization...   

                                              Article              Author  
0   Wyoming Gov. Mark Gordon gives the State of th...          Will Brown  
1   Drivers line up to receive the first and secon...       Chris Boyette  
2   The Moderna building in Cambridge, Massachuset...  Lauren Mascarenhas  
3   In this June 9, 2020 file image, Houston Polic...         Josiah Ryan  
4   The Centers for Medicare & Medicaid Services o...  Lauren Mascarenhas  
5   A healthcare worker arrives in an ambulance br...           Reverdosa  
6   Today marks one year since the Covid-19 contai...           No Author  
7    Andrew Harnik/APThe United States is now on t...   Jacqueline Howard  
8   President Biden on Wednesday applauded the col...   Jacqueline Howard  
9    Mandel Ngan/AFP/Getty ImagesPresident Biden s...           No Author  
10  About 598,523 Americans will have died of coro...  Lauren Mascarenhas  
11  CNN's Van Jones said Thursday that President B...        Leinz Vales   
12   Mandel Ngan/AFP/Getty ImagesPresident Biden s...      Maegan Vazquez  
13  President Biden admitted that many Americans h...      Nikki Carvajal  
14  President Biden said that the federal governme...      Maegan Vazquez  
15  President Biden concluded his first primetime ...        Josiah Ryan   
16   Mandel Ngan/AFP/Getty ImagesPresident Biden c...         Leinz Vales  
17  President Joe Biden looks at a card he pulled ...      Nikki Carvajal  
18   CNNUS Education Secretary Miguel Cardona says...    Elizabeth Stuart  
19   CNNBecky Pringle, president of the National E...           No Author  
20  CNN asked teachers, students and parents to su...           No Author  
21   CNNMiguel Cardona's top priority as President...           No Author  
22  Outside view of the closed AMC Theater, amid t...     Alexandra Meeks  
23  Dr. Anthony Fauci, director of the National In

# All DataBase

In [84]:
#Appending news1_df,news2_df and news3_df to df
documents = pd.DataFrame()
documents = documents.append(news1_df, ignore_index=True)
documents = documents.append(news2_df, ignore_index=True)
documents = documents.append(news3_df, ignore_index=True)
documents

Source        Date  \
0   The Guardian  2021-03-12   
1   The Guardian  2021-03-12   
2   The Guardian  2021-03-12   
3   The Guardian  2021-03-12   
4   The Guardian  2021-03-12   
..           ...         ...   
62           CNN  2021-03-12   
63           CNN  2021-03-12   
64           CNN  2021-03-12   
65           CNN  2021-03-12   
66           CNN  2021-03-12   

                                                Title  \
0   Rory McIlroy: Chasing Bryson DeChambeau’s powe...   
1   Australia commits $100m to Covid vaccine deal ...   
2   Minneapolis to pay George Floyd's family $27m ...   
3   New York senators urge Cuomo to resign after g...   
4   High school announcer caught by hot mic blames...   
..                                                ...   
62  Los Angeles County to reopen indoor dining, mo...   
63  Given what we know now about the pandemic, the...   
64  CDC removes three-month cap on fully vaccinate...   
65  Treasury Department confirms first batch of Co...   
66  Report: AstraZeneca will seek US authorization...   

                                              Article  \
0   While Rory McIlroy’s struggles go on, Lee West...   
1   A historic first meeting of leaders of the Qua...   
2   The city of Minneapolis has agreed to pay $27m...   
3   New York’s two US senators, Chuck Schumer, who...   
4   An announcer for a live stream of an Oklahoma ...   
..                                                ...   
62  Outside view of the closed AMC Theater, amid t...   
63  Dr. Anthony Fauci, director of the National In...   
64  The US Centers for Disease Control and Prevent...   
65  The Treasury Department confirmed the first ba...   
66  Empty phials of the Astra-Zeneca Covid-19 vacc...   

                                        Author  
0                                  Ewan Murray  
1            Graham Readfearn and Daniel Hurst  
2   Amudalat Ajasa in Minneapolis and agencies  
3   Daniel Strauss, Oliver Milman and agencies  
4              Bryan Armen Graham and agencies  
..                                         ...  
62                             Alexandra Meeks  
63                            Christopher Rios  
64                            Michael Nedelman  
65                                 Ross Levitt  
66                              John Bonifield  

[67 rows x 5 columns]

# Text Processing

In [152]:
def removeURLFromText(text):
    result = re.sub(r"http\S+", "", text)
    result = result.strip()
    return result

In [153]:
processed_docs = documents['Article'].map(removeURLFromText)
processed_docs

0     While Rory McIlroy’s struggles go on, Lee West...
1     A historic first meeting of leaders of the Qua...
2     The city of Minneapolis has agreed to pay $27m...
3     New York’s two US senators, Chuck Schumer, who...
4     An announcer for a live stream of an Oklahoma ...
                            ...                        
62    Outside view of the closed AMC Theater, amid t...
63    Dr. Anthony Fauci, director of the National In...
64    The US Centers for Disease Control and Prevent...
65    The Treasury Department confirmed the first ba...
66    Empty phials of the Astra-Zeneca Covid-19 vacc...
Name: Article, Length: 67, dtype: object

In [154]:
def preprocess(text):
    result = []
    for token in gensim.utils.simple_preprocess(text):
        if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 3:
            result.append(lemmatize_stemming(token))
    return result

In [155]:
nltk.download('wordnet')

def lemmatize_stemming(text):
    return WordNetLemmatizer().lemmatize(text, pos='v')

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\pc\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [156]:
processed_docs = processed_docs.map(preprocess)
processed_docs

0     [rory, mcilroy, struggle, westwood, outstandin...
1     [historic, meet, leaders, quad, informal, grou...
2     [city, minneapolis, agree, settle, civil, laws...
3     [york, senators, chuck, schumer, senate, major...
4     [announcer, live, stream, oklahoma, girls, hig...
                            ...                        
62    [outside, view, close, theater, amid, coronavi...
63    [anthony, fauci, director, national, institute...
64    [center, disease, control, prevention, remove,...
65    [treasury, department, confirm, batch, payment...
66    [phials, astra, zeneca, covid, vaccine, vaccin...
Name: Article, Length: 67, dtype: object

In [157]:
dictionary = gensim.corpora.Dictionary(processed_docs)

In [158]:
for x in range(0,20):
    print(x,":",dictionary[x])

0 : able
1 : add
2 : admit
3 : alongside
4 : answer
5 : appreciate
6 : arnold
7 : ask
8 : aspirations
9 : ball
10 : basis
11 : birthday
12 : bryson
13 : care
14 : championship
15 : chris
16 : claim
17 : comfortably
18 : continue
19 : control


In [162]:
dictionary.filter_extremes(no_below=15, no_above=0.5, keep_n=100000)

In [163]:
for x in range(0,20):
    print(x,":",dictionary[x])

0 : add
1 : go
2 : hard
3 : help
4 : home
5 : like
6 : long
7 : mean
8 : need
9 : people
10 : play
11 : start
12 : take
13 : think
14 : time
15 : work
16 : year
17 : years
18 : biden
19 : call


In [164]:
dictionary.cfs

{12: 35,
 0: 36,
 10: 46,
 7: 23,
 5: 57,
 16: 56,
 11: 29,
 6: 23,
 14: 73,
 13: 29,
 9: 79,
 1: 48,
 3: 22,
 8: 25,
 4: 26,
 15: 41,
 2: 20,
 17: 23,
 27: 59,
 21: 54,
 20: 23,
 26: 17,
 19: 37,
 18: 48,
 28: 28,
 24: 23,
 22: 46,
 25: 32,
 23: 21,
 33: 46,
 31: 33,
 30: 27,
 34: 58,
 32: 19,
 29: 28,
 35: 48,
 40: 28,
 38: 45,
 36: 29,
 37: 26,
 39: 35,
 41: 24,
 42: 25,
 43: 21,
 45: 39,
 44: 61,
 46: 29,
 47: 25,
 49: 26,
 48: 21,
 50: 35}

In [165]:
dictionary.dfs

{12: 27,
 0: 18,
 10: 19,
 7: 15,
 5: 27,
 16: 25,
 11: 21,
 6: 15,
 14: 33,
 13: 16,
 9: 33,
 1: 27,
 3: 15,
 8: 17,
 4: 16,
 15: 24,
 2: 17,
 17: 16,
 27: 19,
 21: 22,
 20: 16,
 26: 15,
 19: 21,
 18: 17,
 28: 19,
 24: 17,
 22: 25,
 25: 21,
 23: 16,
 33: 18,
 31: 18,
 30: 17,
 34: 27,
 32: 15,
 29: 19,
 35: 26,
 40: 15,
 38: 19,
 36: 17,
 37: 16,
 39: 18,
 41: 18,
 42: 15,
 43: 15,
 45: 25,
 44: 19,
 46: 17,
 47: 15,
 49: 15,
 48: 18,
 50: 17}

In [166]:
bow_corpus = [dictionary.doc2bow(doc) for doc in processed_docs]

In [167]:
bow_corpus

[[(0, 3),
  (1, 1),
  (2, 1),
  (3, 2),
  (4, 1),
  (5, 2),
  (6, 1),
  (7, 1),
  (8, 1),
  (9, 2),
  (10, 1),
  (11, 1),
  (12, 1),
  (13, 2),
  (14, 1),
  (15, 3),
  (16, 1),
  (17, 1)],
 [(3, 1),
  (6, 1),
  (8, 1),
  (15, 1),
  (18, 4),
  (19, 2),
  (20, 1),
  (21, 1),
  (22, 2),
  (23, 1),
  (24, 1),
  (25, 1),
  (26, 1),
  (27, 2),
  (28, 1)],
 [(0, 3),
  (1, 1),
  (2, 1),
  (5, 1),
  (8, 2),
  (9, 4),
  (12, 1),
  (15, 2),
  (16, 1),
  (17, 1),
  (19, 1),
  (22, 1),
  (24, 1),
  (25, 1),
  (28, 2),
  (29, 1),
  (30, 3),
  (31, 3),
  (32, 1),
  (33, 5),
  (34, 1)],
 [(0, 3),
  (1, 1),
  (4, 3),
  (6, 1),
  (7, 3),
  (8, 2),
  (9, 2),
  (10, 1),
  (12, 1),
  (16, 1),
  (18, 1),
  (19, 5),
  (21, 3),
  (22, 2),
  (26, 1),
  (27, 8),
  (28, 1),
  (35, 3),
  (36, 2),
  (37, 1),
  (38, 3),
  (39, 1),
  (40, 2)],
 [(0, 1),
  (1, 2),
  (2, 1),
  (5, 1),
  (6, 1),
  (8, 1),
  (10, 2),
  (15, 1),
  (19, 2),
  (24, 2),
  (26, 1),
  (27, 4),
  (31, 5),
  (33, 2),
  (34, 1),
  (40, 2),
  (41

In [168]:
tfidf = models.TfidfModel(bow_corpus)

In [169]:
corpus_tfidf = tfidf[bow_corpus]
for x in corpus_tfidf:
    print(x)

[(0, 0.4856774233211091), (1, 0.11194900053384799), (2, 0.16893300565518413), (3, 0.3687001424806098), (4, 0.1764004896808975), (5, 0.22389800106769597), (6, 0.1843500712403049), (7, 0.1843500712403049), (8, 0.16893300565518413), (9, 0.1744624691701206), (10, 0.15523270322772614), (11, 0.14290484689444663), (12, 0.11194900053384799), (13, 0.352800979361795), (14, 0.0872312345850603), (15, 0.3793710473231274), (16, 0.12142873546772448), (17, 0.1764004896808975)]
[(3, 0.18488120614635792), (6, 0.18488120614635792), (8, 0.16941972212610407), (15, 0.1268213537686124), (18, 0.6776788885044163), (19, 0.28663314616858737), (20, 0.17690872087866166), (21, 0.13756992545796196), (22, 0.24355717275352654), (23, 0.17690872087866166), (24, 0.16941972212610407), (25, 0.14331657308429369), (26, 0.18488120614635792), (27, 0.311359894932625), (28, 0.1556799474663125)]
[(0, 0.33947391863568066), (1, 0.0782489860012431), (2, 0.11807909254771494), (5, 0.0782489860012431), (8, 0.23615818509542988), (9, 0.2

In [170]:
df = documents.copy()
df

Source        Date  \
0   The Guardian  2021-03-12   
1   The Guardian  2021-03-12   
2   The Guardian  2021-03-12   
3   The Guardian  2021-03-12   
4   The Guardian  2021-03-12   
..           ...         ...   
62           CNN  2021-03-12   
63           CNN  2021-03-12   
64           CNN  2021-03-12   
65           CNN  2021-03-12   
66           CNN  2021-03-12   

                                                Title  \
0   Rory McIlroy: Chasing Bryson DeChambeau’s powe...   
1   Australia commits $100m to Covid vaccine deal ...   
2   Minneapolis to pay George Floyd's family $27m ...   
3   New York senators urge Cuomo to resign after g...   
4   High school announcer caught by hot mic blames...   
..                                                ...   
62  Los Angeles County to reopen indoor dining, mo...   
63  Given what we know now about the pandemic, the...   
64  CDC removes three-month cap on fully vaccinate...   
65  Treasury Department confirms first batch of Co...   
66  Report: AstraZeneca will seek US authorization...   

                                              Article  \
0   While Rory McIlroy’s struggles go on, Lee West...   
1   A historic first meeting of leaders of the Qua...   
2   The city of Minneapolis has agreed to pay $27m...   
3   New York’s two US senators, Chuck Schumer, who...   
4   An announcer for a live stream of an Oklahoma ...   
..                                                ...   
62  Outside view of the closed AMC Theater, amid t...   
63  Dr. Anthony Fauci, director of the National In...   
64  The US Centers for Disease Control and Prevent...   
65  The Treasury Department confirmed the first ba...   
66  Empty phials of the Astra-Zeneca Covid-19 vacc...   

                                        Author  
0                                  Ewan Murray  
1            Graham Readfearn and Daniel Hurst  
2   Amudalat Ajasa in Minneapolis and agencies  
3   Daniel Strauss, Oliver Milman and agencies  
4              Bryan Armen Graham and agencies  
..                                         ...  
62                             Alexandra Meeks  
63                            Christopher Rios  
64                            Michael Nedelman  
65                                 Ross Levitt  
66                              John Bonifield  

[67 rows x 5 columns]

In [171]:
art_bow = []
for i in range(len(corpus_tfidf)):
    art_bow.append(corpus_tfidf[i])
art_bow

[[(0, 0.4856774233211091),
  (1, 0.11194900053384799),
  (2, 0.16893300565518413),
  (3, 0.3687001424806098),
  (4, 0.1764004896808975),
  (5, 0.22389800106769597),
  (6, 0.1843500712403049),
  (7, 0.1843500712403049),
  (8, 0.16893300565518413),
  (9, 0.1744624691701206),
  (10, 0.15523270322772614),
  (11, 0.14290484689444663),
  (12, 0.11194900053384799),
  (13, 0.352800979361795),
  (14, 0.0872312345850603),
  (15, 0.3793710473231274),
  (16, 0.12142873546772448),
  (17, 0.1764004896808975)],
 [(3, 0.18488120614635792),
  (6, 0.18488120614635792),
  (8, 0.16941972212610407),
  (15, 0.1268213537686124),
  (18, 0.6776788885044163),
  (19, 0.28663314616858737),
  (20, 0.17690872087866166),
  (21, 0.13756992545796196),
  (22, 0.24355717275352654),
  (23, 0.17690872087866166),
  (24, 0.16941972212610407),
  (25, 0.14331657308429369),
  (26, 0.18488120614635792),
  (27, 0.311359894932625),
  (28, 0.1556799474663125)],
 [(0, 0.33947391863568066),
  (1, 0.0782489860012431),
  (2, 0.1180790

In [172]:
df['article_body_bow'] = art_bow

In [173]:
df

Source        Date  \
0   The Guardian  2021-03-12   
1   The Guardian  2021-03-12   
2   The Guardian  2021-03-12   
3   The Guardian  2021-03-12   
4   The Guardian  2021-03-12   
..           ...         ...   
62           CNN  2021-03-12   
63           CNN  2021-03-12   
64           CNN  2021-03-12   
65           CNN  2021-03-12   
66           CNN  2021-03-12   

                                                Title  \
0   Rory McIlroy: Chasing Bryson DeChambeau’s powe...   
1   Australia commits $100m to Covid vaccine deal ...   
2   Minneapolis to pay George Floyd's family $27m ...   
3   New York senators urge Cuomo to resign after g...   
4   High school announcer caught by hot mic blames...   
..                                                ...   
62  Los Angeles County to reopen indoor dining, mo...   
63  Given what we know now about the pandemic, the...   
64  CDC removes three-month cap on fully vaccinate...   
65  Treasury Department confirms first batch of Co...   
66  Report: AstraZeneca will seek US authorization...   

                                              Article  \
0   While Rory McIlroy’s struggles go on, Lee West...   
1   A historic first meeting of leaders of the Qua...   
2   The city of Minneapolis has agreed to pay $27m...   
3   New York’s two US senators, Chuck Schumer, who...   
4   An announcer for a live stream of an Oklahoma ...   
..                                                ...   
62  Outside view of the closed AMC Theater, amid t...   
63  Dr. Anthony Fauci, director of the National In...   
64  The US Centers for Disease Control and Prevent...   
65  The Treasury Department confirmed the first ba...   
66  Empty phials of the Astra-Zeneca Covid-19 vacc...   

                                        Author  \
0                                  Ewan Murray   
1            Graham Readfearn and Daniel Hurst   
2   Amudalat Ajasa in Minneapolis and agencies   
3   Daniel Strauss, Oliver Milman and agencies   
4              Bryan Armen Graham and agencies   
..                                         ...   
62                             Alexandra Meeks   
63                            Christopher Rios   
64                            Michael Nedelman   
65                                 Ross Levitt   
66                              John Bonifield   

                                     article_body_bow  
0   [(0, 0.4856774233211091), (1, 0.11194900053384...  
1   [(3, 0.18488120614635792), (6, 0.1848812061463...  
2   [(0, 0.33947391863568066), (1, 0.0782489860012...  
3   [(0, 0.24048590981062415), (1, 0.0554321777233...  
4   [(0, 0.11133741365868192), (1, 0.1539801306292...  
..                                                ...  
62  [(9, 0.22136481628911955), (15, 0.160453616176...  
63  [(5, 0.10619898491438524), (9, 0.2482523788935...  
64  [(4, 0.2135087936883892), (7, 0.22313068063522...  
65  [(1, 0.19219252699330092), (11, 0.490674209028...  
66  [(9, 0.09816861738026285), (18, 0.190114466153...  

[67 rows x 6 columns]

In [185]:
data1 = df.to_json(orient='records')
parsed = json.loads(data1)
json.dumps(parsed, indent=4) 
with open('news_scape.json', 'w') as json_file:
    json.dump(parsed, json_file)

In [186]:
parsed

[{'Source': 'The Guardian',
  'Date': '2021-03-12',
  'Title': 'Rory McIlroy: Chasing Bryson DeChambeau’s power has cost me',
  'Article': 'While Rory McIlroy’s struggles go on, Lee Westwood’s outstanding form continued. Just days after taking Bryson DeChambeau to the final hole at the Arnold Palmer Invitational, the Englishman added a 66 to his first-round 69 and leads by one shot from Matthew Fitzpatrick at the Players Championship. McIlroy has admitted a desire to add more length to his game, fuelled in part by DeChambeau’s power play at the 2020 US Open, has triggered technical problems that were visible here. A second round of 75 at Sawgrass, added to Thursday’s 79, meant McIlroy comfortably missed the cut. Afterwards, he expanded on the basis for his swing issues. “Probably, like October last year, doing a little bit of speed training, started getting sucked into that stuff, swing got flat, long and too rotational,” said McIlroy. “Obviously I added some speed and am hitting the b

In [190]:
with open('article_body_bow.json', 'w') as json_file:
    json.dump(art_bow, json_file)